In [4]:
import torch
import torchvision
import rasterio
import detectree2
from detectree2.preprocessing.tiling import tile_data
from detectree2.models.outputs import project_to_geojson, stitch_crowns, clean_crowns
from detectree2.models.predict import predict_on_data
from detectree2.models.train import setup_cfg
from detectron2.engine import DefaultPredictor
import cv2
import os
from osgeo import gdal
import shutil
import numpy as np
import geopandas as gpd
import pandas as pd
from pathlib import Path
from shapely.geometry import Polygon, box, shape
from rasterio.crs import CRS
import os
from datetime import datetime, timedelta
from os.path import join
from shapely.ops import unary_union
import math

In [5]:
def is_completely_covered_and_touching(covering_polygon, covered_polygon):
    """
    Check if one polygon completely covers another and they share boundary parts.

    Parameters:
    covering_polygon (Polygon): The polygon that might be covering another.
    covered_polygon (Polygon): The polygon that might be covered.

    Returns:
    bool: True if covering_polygon completely covers covered_polygon and they share boundaries, False otherwise.
    """
    # Check if the covering polygon completely covers the covered polygon
    covers = covering_polygon.covers(covered_polygon)
    
    # Check if the boundaries touch, which implies some boundary parts are shared
    # This requires examining the boundaries as LineStrings

    
    boundary_touch = covering_polygon.boundary.intersects(covered_polygon.boundary) and not covering_polygon.boundary.touches(covered_polygon.boundary)

    return covers and boundary_touch

In [6]:

def extract_nonborder_polygons(folder_path):
    # List all GeoJSON files in the specified directory
    geojson_files = [os.path.join(folder_path, f) for f in os.listdir(folder_path) if f.endswith('.geojson')]
    
    # List to hold dataframes
    non_border_polygons = gpd.GeoDataFrame()

    
    # Process each file
    for file_path in geojson_files:
        # Load the GeoJSON file into a GeoDataFrame
        gdf = gpd.read_file(file_path)

        # Determine overall bounding box of the tile
        bounds = gdf.total_bounds
        tile_box = box(*bounds)  # Create a shapely box from the bounds

        
        for i in range(len(gdf)):
            # Check if the polygon is completely covered by other polygons
           if (not is_completely_covered_and_touching(tile_box, gdf.geometry.iloc[i])):
            non_border_polygons = pd.concat([non_border_polygons, gdf.iloc[[i]]])
  
    
    

        # Filter out polygons that touch and do not touch the border
       
    
    # Return list of GeoDataFrames containing non-border polygons for further processing if necessary
    return non_border_polygons



In [7]:
# First overlay between gdf1 and gdf2
gdf1 = extract_nonborder_polygons('result_polygons_noshift')
gdf2 = extract_nonborder_polygons('result_polygons_shiftx')
gdf3 = extract_nonborder_polygons('result_polygons_shifty')
gdf4 = extract_nonborder_polygons('result_polygons_shiftxy')


#gdf1['geometry'] = gdf1['geometry'].simplify(tolerance=0.1, preserve_topology=True)
#gdf2['geometry'] = gdf2['geometry'].simplify(tolerance=0.1, preserve_topology=True)

union_12 = gpd.overlay(gdf1, gdf2, how='union')

union_34 = gpd.overlay(gdf3, gdf4, how='union')

final_union = gpd.overlay(union_12, union_34, how='union')

# Optional: Simplify geometries if needed (e.g., for visualization or reducing complexity)

# Optional: Remove duplicates based on exact geometry matching
# This might be necessary if the same geometry appears more than once
final_union = final_union.drop_duplicates(subset=['geometry'])

# Save the result to a new GeoJSON file or use it directly
final_union.to_file("final_union_flight1.geojson", driver='GeoJSON')
final_union.to_file("final_union_flight1.shp", driver='ESRI Shapefile')



/opt/homebrew/Caskroom/miniconda/base/envs/detectree2/lib/python3.11/site-packages/geopandas/geodataframe.py:1816: FutureWarning: `unary_union` returned None due to all-None GeoSeries. In future, `unary_union` will return 'GEOMETRYCOLLECTION EMPTY' instead.
  merged_geom = block.unary_union
/var/folders/ry/qhyv3_sd28n3rzthk9tzgl5r0000gn/T/ipykernel_28356/2736563917.py:11: UserWarning: `keep_geom_type=True` in overlay resulted in 54409 dropped geometries of different geometry types than df1 has. Set `keep_geom_type=False` to retain all geometries
  union_12 = gpd.overlay(gdf1, gdf2, how='union')
/opt/homebrew/Caskroom/miniconda/base/envs/detectree2/lib/python3.11/site-packages/geopandas/geodataframe.py:1816: FutureWarning: `unary_union` returned None due to all-None GeoSeries. In future, `unary_union` will return 'GEOMETRYCOLLECTION EMPTY' instead.
  merged_geom = block.unary_union
/var/folders/ry/qhyv3_sd28n3rzthk9tzgl5r0000gn/T/ipykernel_28356/2736563917.py:13: UserWarning: `keep_geom

In [ ]:
def extract_nonborder_polygons_list(folder_path):
    # List all GeoJSON files in the specified directory
    geojson_files = [os.path.join(folder_path, f) for f in os.listdir(folder_path) if f.endswith('.geojson')]
    
    # List to hold dataframes
    non_border_polygons = []
    
    # Process each file
    for file_path in geojson_files:
        # Load the GeoJSON file into a GeoDataFrame
        gdf = gpd.read_file(file_path)


        
        # Determine overall bounding box of the tile
        bounds = gdf.total_bounds
        tile_box = box(*bounds)  # Create a shapely box from the bounds

        non_border_polygons = []

        for i in range(len(gdf)):
            # Check if the polygon is completely covered by other polygons
           if (not is_completely_covered_and_touching(tile_box, gdf.geometry.iloc[i])):
            non_border_polygons = non_border_polygons + [gdf.geometry.iloc[i]]
    
        # Filter out polygons that touch and do not touch the border
       
    
    # Return list of GeoDataFrames containing non-border polygons for further processing if necessary
    return non_border_polygons



In [ ]:
# First overlay between gdf1 and gdf2
list1 = extract_nonborder_polygons_list('result_polygons_noshift')
list2 = extract_nonborder_polygons_list('result_polygons_shiftx')
#gdf3 = extract_nonborder_polygons('y_shifted_polygons')

union = []

for i in range(len(list1)):
    for j in range(len(list2)):
        if (list1[i].intersects(list2[j]) or list1[i].covers(list2[j] or list1[i].within(list2[j]))) :
            current = unary_union([list1[i],(list2[j])])
            union.append(current)
        

#union_12 = gpd.overlay(gdf1, gdf2, how='union')
final_union = gpd.GeoDataFrame(geometry=union)
nonborder_pol1 = gpd.GeoDataFrame(geometry=list1)
nonborder_pol2 = gpd.GeoDataFrame(geometry=list2)

# Second overlay with gdf3
#final_union = gpd.overlay(union_12, gdf3, how='union')

# Optional: Simplify geometries if needed (e.g., for visualization or reducing complexity)

# Optional: Remove duplicates based on exact geometry matching
# This might be necessary if the same geometry appears more than once
final_union = final_union.drop_duplicates(subset=['geometry'])

# Save the result to a new GeoJSON file or use it directly
final_union.to_file("final_union_geojson.geojson", driver='GeoJSON')
final_union.to_file("final_union_0shapefile.shp", driver='ESRI Shapefile')

nonborder_pol1.to_file("nonborder_pol1.shp", driver='ESRI Shapefile')
nonborder_pol2.to_file("nonborder_pol2.shp", driver='ESRI Shapefile')